Importing Libraries

In [1]:
#Import packages
import pandas as pd
import numpy as np
import MetaTrader5 as mt5
from   datetime import datetime
import pandas_ta as ta
import time

Setting Up Trading Session

In [2]:
#Account login details
login = 123124124
password = "Enter Your Password"
server = "Enter Your Broker"
symbol = "EURUSD"
#What timeframe are we working on?
timeframe = mt5.TIMEFRAME_M1
#This data frame will store the most recent price update
last_close = pd.DataFrame()
#We may not always enter at the price we want, how much deviation can we tolerate?
deviation = 100
#The size of our positions
volume = 0
#How many times the minimum volume should our positions be
lot_multiple = 1

Logging In

In [10]:
#Login
if(mt5.initialize(login=login,password=password,server=server)):
    print("Logged in successfully")
else:
    print("Failed to login")

Logged in successfully


Getting Market Details

In [11]:
#Setup trading volume
symbols = mt5.symbols_get()
for index,symbol in enumerate(symbols):
    if symbol.name == "EURUSD":
        print(f"{symbol.name} has minimum volume: {symbol.volume_min}")
        volume = symbol.volume_min * lot_multiple

EURUSD has minimum volume: 0.01


Specify how much data we need

In [12]:
#Specify date range of data to be modelled
date_start = datetime(2020,1,1)
date_end = datetime.now()

Fetch Market data

In [13]:
#Fetch market data
market_data = pd.DataFrame(mt5.copy_rates_range("EURUSD",timeframe,date_start,date_end))
market_data["time"] = pd.to_datetime(market_data["time"],unit='s')
#Add simple moving average technical indicator
market_data.ta.sma(length=20,append=True)
#Delete missing rows
market_data.dropna(inplace=True)
#Inspect the dataframe
market_data

time     open     high      low    close  tick_volume  \
19      2020-01-01 22:18:00  1.12144  1.12150  1.12141  1.12144            6   
20      2020-01-01 22:19:00  1.12144  1.12144  1.12136  1.12140           21   
21      2020-01-01 22:20:00  1.12138  1.12143  1.12134  1.12138           15   
22      2020-01-01 22:21:00  1.12138  1.12149  1.12136  1.12145           35   
23      2020-01-01 22:22:00  1.12145  1.12145  1.12145  1.12145            1   
...                     ...      ...      ...      ...      ...          ...   
1651906 2024-06-13 11:23:00  1.07914  1.07916  1.07904  1.07914          102   
1651907 2024-06-13 11:24:00  1.07914  1.07915  1.07907  1.07913          128   
1651908 2024-06-13 11:25:00  1.07912  1.07920  1.07901  1.07901          107   
1651909 2024-06-13 11:26:00  1.07901  1.07917  1.07901  1.07913           71   
1651910 2024-06-13 11:27:00  1.07913  1.07925  1.07910  1.07922           82   

         spread  real_volume    SMA_20  
19           14            0  1.121113  
20            9            0  1.121185  
21           10            0  1.121201  
22           12            0  1.121212  
23           23            0  1.121218  
...         ...          ...       ...  
1651906       0            0  1.079338  
1651907       0            0  1.079329  
1651908       0            0  1.079317  
1651909       0            0  1.079314  
1651910       0            0  1.079306  

[1651892 rows x 9 columns]

How much time should be between the candles?

In [14]:
#Define how far ahead we are looking
look_ahead = 1

Calculate transition probabilities

In [15]:
#Count the number of times price was above the moving average
up = market_data.loc[market_data["close"] > market_data["SMA_20"]].shape[0]

#Count the number of times price was below the moving average
down = market_data.loc[market_data["close"] < market_data["SMA_20"]].shape[0]

#Count the number of times price was above the moving average and remained above it
up_and_up = (market_data.loc[( (market_data["close"] > market_data["SMA_20"]) & (market_data["close"].shift(-look_ahead) > market_data["SMA_20"].shift(-look_ahead)) )].shape[0]) / up

#Count the number of times price was below the moving average and remained below it
down_and_down = (market_data.loc[( (market_data["close"] < market_data["SMA_20"]) & (market_data["close"].shift(-look_ahead) < market_data["SMA_20"].shift(-look_ahead)) )].shape[0]) / down

In [16]:
transition_matrix = pd.DataFrame({
    "UP":[up_and_up,(1-up_and_up)],
    "DOWN":[(1-down_and_down),down_and_down]
},index=['UP','DOWN'])

In [17]:
transition_matrix

UP      DOWN
UP    0.875892  0.126748
DOWN  0.124108  0.873252

Pay Attention To The Design Pattern

In [18]:
transition_matrix = pd.DataFrame({
    "UP":["UP AND UP","UP AND DOWN"],
    "DOWN":["DOWN AND UP","DOWN AND DOWN"]
},index=['UP','DOWN'])

In [19]:
transition_matrix

UP           DOWN
UP      UP AND UP    DOWN AND UP
DOWN  UP AND DOWN  DOWN AND DOWN

In [148]:
def get_prices():
    start = datetime(2024,6,1)
    end   = datetime.now()
    data  = pd.DataFrame(mt5.copy_rates_range("EURUSD",timeframe,start,end))
    #Add simple moving average technical indicator
    data.ta.sma(length=20,append=True)
    #Delete missing rows
    data.dropna(inplace=True)
    data['time'] = pd.to_datetime(data['time'],unit='s')
    data.set_index('time',inplace=True)
    return(data.iloc[-1,:])

In [149]:
print(get_prices())

open            1.075680
high            1.075680
low             1.075610
close           1.075610
tick_volume    11.000000
spread          0.000000
real_volume     0.000000
SMA_20          1.075665
Name: 2024-06-10 09:10:00, dtype: float64


In [150]:
def get_state(current_data):
    #Price is above the moving average, UP state
    if(current_data["close"]  > current_data["SMA_20"]):
        return(1)
    #Price is below the moving average, DOWN state
    elif(current_data["close"] < current_data["SMA_20"]):
        return(2)

In [151]:
def get_action(current_state):
    if(current_state == 1):
        if(transition_matrix.iloc[0,0] > transition_matrix.iloc[0,1]):
            print("The market is above the moving average and has strong trends, buy")
            print("Opening a BUY position")
            mt5.Buy("EURUSD",volume)
        elif(transition_matrix.iloc[0,0] < transition_matrix.iloc[0,1]):
            print("The market is above the moving average and has strong mean reverting moves, sell")
            print("Opening a sell position")
            mt5.Sell("EURUSD",volume)
    elif(current_state == 2):
        if(transition_matrix.iloc[1,0] > transition_matrix.iloc[1,1]):
            print("The market is below the moving average and has strong mean reverting moves, buy")
            print("Opening a BUY position")
            mt5.Buy("EURUSD",volume)
        elif(transition_matrix.iloc[1,0] < transition_matrix.iloc[1,1]):
            print("The market is below the moving average and has strong trends, sell")
            print("Opening a sell position")
            mt5.Sell("EURUSD",volume)

In [137]:
while True:
    #Get data on the current state of our terminal and our portfolio
    positions = mt5.positions_total()
    #If we have no open positions then we can open one
    if(positions == 0):
        get_action(get_state(get_prices()))
    #If we have finished all checks then we can wait for one day before checking our positions again
    time.sleep(60)

The market is below the moving average and has strong trends, sell
Opening a sell position


KeyboardInterrupt: 

Changing The Symbol

In [29]:
#Changing the symbol
#Fetch market data
market_data = pd.DataFrame(mt5.copy_rates_range("Boom 1000 Index",timeframe,date_start,date_end))
market_data["time"] = pd.to_datetime(market_data["time"],unit='s')
#Add simple moving average technical indicator
market_data.ta.sma(length=20,append=True)
#Delete missing rows
market_data.dropna(inplace=True)
#Inspect the dataframe
market_data

time       open       high        low      close  \
19      2019-12-31 22:19:00   9847.148   9847.148   9846.609   9846.609   
20      2019-12-31 22:20:00   9846.603   9846.603   9846.008   9846.008   
21      2019-12-31 22:21:00   9845.995   9845.995   9845.441   9845.441   
22      2019-12-31 22:22:00   9845.423   9845.423   9844.895   9844.895   
23      2019-12-31 22:23:00   9844.893   9844.893   9844.247   9844.247   
...                     ...        ...        ...        ...        ...   
2162143 2024-06-13 08:31:00  15598.381  15598.381  15597.393  15597.393   
2162144 2024-06-13 08:32:00  15597.364  15597.364  15596.512  15596.512   
2162145 2024-06-13 08:33:00  15596.511  15596.511  15595.496  15595.496   
2162146 2024-06-13 08:34:00  15595.477  15595.477  15594.510  15594.510   
2162147 2024-06-13 08:35:00  15594.500  15594.500  15593.612  15593.612   

         tick_volume  spread  real_volume       SMA_20  
19                58     980            0   9852.06690  
20                59     980            0   9851.49385  
21                58     980            0   9850.92045  
22                58     980            0   9850.34570  
23                57     980            0   9849.76620  
...              ...     ...          ...          ...  
2162143           60    1550            0  15605.97155  
2162144           55    1550            0  15605.06060  
2162145           58    1550            0  15604.15195  
2162146           60    1550            0  15603.24095  
2162147           59    1550            0  15602.33140  

[2162129 rows x 9 columns]

In [30]:
#Count the number of times price was above the moving average
up = market_data.loc[market_data["close"] > market_data["SMA_20"]].shape[0]

#Count the number of times price was below the moving average
down = market_data.loc[market_data["close"] < market_data["SMA_20"]].shape[0]

#Count the number of times price was above the moving average and remained above it
up_and_up = (market_data.loc[( (market_data["close"] > market_data["SMA_20"]) & (market_data["close"].shift(-look_ahead) > market_data["SMA_20"].shift(-look_ahead)) )].shape[0]) / up

#Count the number of times price was below the moving average and remained below it
down_and_down = (market_data.loc[( (market_data["close"] < market_data["SMA_20"]) & (market_data["close"].shift(-look_ahead) < market_data["SMA_20"].shift(-look_ahead)) )].shape[0]) / down

In [31]:
transition_matrix = pd.DataFrame({
    "UP":[up_and_up,(1-down_and_down)],
    "DOWN":[(1-up_and_up),down_and_down]
},index=['UP','DOWN'])

In [32]:
transition_matrix

UP      DOWN
UP    0.925602  0.074398
DOWN  0.042849  0.957151

Changing The Period

In [33]:
#Changing the symbol
#Fetch market data
market_data = pd.DataFrame(mt5.copy_rates_range("EURUSD",timeframe,date_start,date_end))
market_data["time"] = pd.to_datetime(market_data["time"],unit='s')
#Add simple moving average technical indicator
market_data.ta.sma(length=2,append=True)
#Delete missing rows
market_data.dropna(inplace=True)
#Inspect the dataframe
market_data

time     open     high      low    close  tick_volume  \
1       2020-01-01 22:00:00  1.12088  1.12121  1.12088  1.12106            6   
2       2020-01-01 22:01:00  1.12106  1.12124  1.12089  1.12124            5   
3       2020-01-01 22:02:00  1.12131  1.12131  1.12131  1.12131            1   
4       2020-01-01 22:03:00  1.12131  1.12131  1.12113  1.12113            5   
5       2020-01-01 22:04:00  1.12113  1.12117  1.12113  1.12117            2   
...                     ...      ...      ...      ...      ...          ...   
1651734 2024-06-13 08:31:00  1.08114  1.08120  1.08109  1.08110           27   
1651735 2024-06-13 08:32:00  1.08110  1.08124  1.08110  1.08113           43   
1651736 2024-06-13 08:33:00  1.08113  1.08114  1.08093  1.08095           46   
1651737 2024-06-13 08:34:00  1.08095  1.08095  1.08077  1.08080           36   
1651738 2024-06-13 08:35:00  1.08080  1.08080  1.08061  1.08067           48   

         spread  real_volume     SMA_2  
1            48            0  1.120515  
2            49            0  1.121150  
3            43            0  1.121275  
4            34            0  1.121220  
5            31            0  1.121150  
...         ...          ...       ...  
1651734       0            0  1.081115  
1651735       0            0  1.081115  
1651736       0            0  1.081040  
1651737       0            0  1.080875  
1651738       0            0  1.080735  

[1651738 rows x 9 columns]

In [35]:
#Count the number of times price was above the moving average
up = market_data.loc[market_data["close"] > market_data["SMA_2"]].shape[0]

#Count the number of times price was below the moving average
down = market_data.loc[market_data["close"] < market_data["SMA_2"]].shape[0]

#Count the number of times price was above the moving average and remained above it
up_and_up = (market_data.loc[( (market_data["close"] > market_data["SMA_2"]) & (market_data["close"].shift(-look_ahead) > market_data["SMA_2"].shift(-look_ahead)) )].shape[0]) / up

#Count the number of times price was below the moving average and remained below it
down_and_down = (market_data.loc[( (market_data["close"] < market_data["SMA_2"]) & (market_data["close"].shift(-look_ahead) < market_data["SMA_2"].shift(-look_ahead)) )].shape[0]) / down

In [36]:
transition_matrix = pd.DataFrame({
    "UP":[up_and_up,(1-down_and_down)],
    "DOWN":[(1-up_and_up),down_and_down]
},index=['UP','DOWN'])

In [37]:
transition_matrix

UP      DOWN
UP    0.455866  0.544134
DOWN  0.546790  0.453210

Changing The Gap

In [38]:
#Define how far ahead we are looking
look_ahead = 100

In [39]:
#Fetch market data
market_data = pd.DataFrame(mt5.copy_rates_range("EURUSD",timeframe,date_start,date_end))
market_data["time"] = pd.to_datetime(market_data["time"],unit='s')
#Add simple moving average technical indicator
market_data.ta.sma(length=20,append=True)
#Delete missing rows
market_data.dropna(inplace=True)
#Inspect the dataframe
market_data

time     open     high      low    close  tick_volume  \
19      2020-01-01 22:18:00  1.12144  1.12150  1.12141  1.12144            6   
20      2020-01-01 22:19:00  1.12144  1.12144  1.12136  1.12140           21   
21      2020-01-01 22:20:00  1.12138  1.12143  1.12134  1.12138           15   
22      2020-01-01 22:21:00  1.12138  1.12149  1.12136  1.12145           35   
23      2020-01-01 22:22:00  1.12145  1.12145  1.12145  1.12145            1   
...                     ...      ...      ...      ...      ...          ...   
1651734 2024-06-13 08:31:00  1.08114  1.08120  1.08109  1.08110           27   
1651735 2024-06-13 08:32:00  1.08110  1.08124  1.08110  1.08113           43   
1651736 2024-06-13 08:33:00  1.08113  1.08114  1.08093  1.08095           46   
1651737 2024-06-13 08:34:00  1.08095  1.08095  1.08077  1.08080           36   
1651738 2024-06-13 08:35:00  1.08080  1.08080  1.08061  1.08067           48   

         spread  real_volume    SMA_20  
19           14            0  1.121113  
20            9            0  1.121185  
21           10            0  1.121201  
22           12            0  1.121212  
23           23            0  1.121218  
...         ...          ...       ...  
1651734       0            0  1.081013  
1651735       0            0  1.081013  
1651736       0            0  1.081006  
1651737       0            0  1.080998  
1651738       0            0  1.080990  

[1651720 rows x 9 columns]

In [40]:
#Count the number of times price was above the moving average
up = market_data.loc[market_data["close"] > market_data["SMA_20"]].shape[0]

#Count the number of times price was below the moving average
down = market_data.loc[market_data["close"] < market_data["SMA_20"]].shape[0]

#Count the number of times price was above the moving average and remained above it
up_and_up = (market_data.loc[( (market_data["close"] > market_data["SMA_20"]) & (market_data["close"].shift(-look_ahead) > market_data["SMA_20"].shift(-look_ahead)) )].shape[0]) / up

#Count the number of times price was below the moving average and remained below it
down_and_down = (market_data.loc[( (market_data["close"] < market_data["SMA_20"]) & (market_data["close"].shift(-look_ahead) < market_data["SMA_20"].shift(-look_ahead)) )].shape[0]) / down

In [41]:
transition_matrix = pd.DataFrame({
    "UP":[up_and_up,(1-down_and_down)],
    "DOWN":[(1-up_and_up),down_and_down]
},index=['UP','DOWN'])

In [42]:
transition_matrix

UP      DOWN
UP    0.502712  0.497288
DOWN  0.507688  0.492312